// can't yet format YamlFrontmatter (["title: Temperature in Germany"; "category: Datasets"; "categoryindex: 1"; "index: 6"], Some { StartLine = 2 StartColumn = 0 EndLine = 6 EndColumn = 8 }) to pynb markdown

[![Binder](/datasets/img/badge-binder.svg)](https://mybinder.org/v2/gh/plotly/Plotly.NET/gh-pages?filepath=06_TemperatureGermany.ipynb)&emsp;
[![Script](/datasets/img/badge-script.svg)](/datasets/06_TemperatureGermany.fsx)&emsp;
[![Notebook](/datasets/img/badge-notebook.svg)](/datasets/06_TemperatureGermany.ipynb)

# The _Deutsche Wetterdienst_ datasets

**Table of contents**

- [Description]()
- [How to use]()
- [Examples]()

## Description

The official website from the ["Deutsche Wetterdienst"](https://www.dwd.de/DE/leistungen/klimadatendeutschland/klimadatendeutschland.html) offers regional climate data with daily or monthly measurements.


## How to use





In [1]:
#r "nuget: Fsharp.Data"
#r "nuget: FSharp.Stats"
#r "nuget: Plotly.NET, 2.0.0-preview.6"
#r "nuget: Deedle"

// Get data from Deutscher Wetterdienst
// Explanation for Abbreviations: https://www.dwd.de/DE/leistungen/klimadatendeutschland/beschreibung_tagesmonatswerte.html
let rawData = FSharp.Data.Http.RequestString @"https://raw.githubusercontent.com/fslaborg/datasets/main/data/WeatherDataAachen-Orsbach_daily_1year.txt"

open System
open System.Text.RegularExpressions

open Deedle

//The data is formatted in a char column-wise structure, to transform it into a seperator-delimited format, we have to do prior formatting:

let processedData = 
    // First separate the huge string in lines
    rawData.Split([|'\n'|], StringSplitOptions.RemoveEmptyEntries)
    // Skip the first 5 rows until the real data starts, also skip the last row (length-2) to remove a "</pre>" at the end
    |> fun arr -> arr.[5..arr.Length-2]
    |> Array.map (fun data -> 
        // Regex pattern that will match groups of whitespace
        let whitespacePattern = @"\s+"
        // This is needed to tell regex to replace hits with a tabulator
        let matchEval = MatchEvaluator(fun _ -> "\t" )
        // The original data columns are separated by different amounts of whitespace.
        // Therefore, we need a flexible string parsing option to replace any amount of whitespace with a single tabulator.
        // This is done with the regex pattern above and the fsharp core library "System.Text.RegularExpressions" 
        let tabseparated = Regex.Replace(data, whitespacePattern, matchEval)
        tabseparated
        // Split each row by tabulator will return rows with an equal amount of values, which we can access.
        |> fun dataStr -> dataStr.Split([|"\t"|], StringSplitOptions.RemoveEmptyEntries)
        |> fun dataArr -> 
            // Second value is the date of measurement, which we will parse to the DateTime type
            DateTime.ParseExact(dataArr.[1], "yyyyMMdd", Globalization.CultureInfo.InvariantCulture),
            // 5th value is minimal temperature at that date.
            float dataArr.[4],
            // 6th value is average temperature over 24 timepoints at that date.
            float dataArr.[5],
            // 7th value is maximal temperature at that date.
            float dataArr.[6]
    )
    // Sort by date
    |> Array.sortBy (fun (day,tn,tm,tx) -> day)
    // Unzip the array of value tuples, to make the different values easier accessible
    |> fun arr -> 
        arr |> Array.map (fun (day,tn,tm,tx) -> day.ToShortDateString()),
        arr |> Array.map (fun (day,tn,tm,tx) -> tm),
        arr |> Array.map (fun (day,tn,tm,tx) -> tx),
        arr |> Array.map (fun (day,tn,tm,tx) -> tn)


([|"03/16/2020"; "03/17/2020"; "03/18/2020"; "03/19/2020"; "03/20/2020";   "03/21/2020"; "03/22/2020"; "03/23/2020"; "03/24/2020"; "03/25/2020";   "03/26/2020"; "03/27/2020"; "03/28/2020"; "03/29/2020"; "03/30/2020";   "03/31/2020"; "04/01/2020"; "04/02/2020"; "04/03/2020"; "04/04/2020";   "04/05/2020"; "04/06/2020"; "04/07/2020"; "04/08/2020"; "04/09/2020";   "04/10/2020"; "04/11/2020"; "04/12/2020"; "04/13/2020"; "04/14/2020";   "04/15/2020"; "04/16/2020"; "04/17/2020"; "04/18/2020"; "04/19/2020";   "04/20/2020"; "04/21/2020"; "04/22/2020"; "04/23/2020"; "04/24/2020";   "04/25/2020"; "04/26/2020"; "04/27/2020"; "04/28/2020"; "04/29/2020";   "04/30/2020"; "05/01/2020"; "05/02/2020"; "05/03/2020"; "05/04/2020";   "05/05/2020"; "05/06/2020"; "05/07/2020"; "05/08/2020"; "05/09/2020";   "05/10/2020"; "05/11/2020"; "05/12/2020"; "05/13/2020"; "05/14/2020";   "05/15/2020"; "05/16/2020"; "05/17/2020"; "05/18/2020"; "05/19/2020";   "05/20/2020"; "05/21/2020"; "05/22/2020"; "05/23/2020"; "05/2

## Examples



In [3]:
open Plotly.NET

// Because our data set is already rather wide we want to move the legend from the right side of the plot
// to the right center. As this function is not defined for fsharp we will use the underlying js bindings (https://plotly.com/javascript/legend/#positioning-the-legend-inside-the-plot).
// Declarative style in F# using underlying DynamicObj
// https://plotly.net/#Declarative-style-in-F-using-the-underlying
let legend = 
    let tmp = Legend()
    tmp?yanchor <- "top"
    tmp?y <- 0.99
    tmp?xanchor <- "left"
    tmp?x <- 0.5
    tmp

/// This function will take 'processedData' as input and return a range chart with a line for the average temperature
/// and a different colored area for the range between minimal and maximal temperature at that date.
let createTempChart (days,tm,tmUpper,tmLower) =
    Chart.Range(
        // data arrays
        days, tm, tmUpper, tmLower,
        StyleParam.Mode.Lines_Markers,
        Color="#3D1244",
        RangeColor="#F99BDE",
        // Name for line in legend
        Name="Average temperature over 24 timepoints each day",
        // Name for lower point when hovering over chart
        LowerName="Min temp",
        // Name for upper point when hovering over chart
        UpperName="Max temp"
    )
    // Configure the chart with the legend from above
    |> Chart.withLegend legend
    // Add name to y axis
    |> Chart.withY_AxisStyle("daily temperature [°C]")
    |> Chart.withSize (1000.,600.)

/// Chart for original data set 
let rawChart =
    processedData 
    |> createTempChart

rawChart |> GenericChart.toChartHTML


<!-- Plotly chart will be drawn inside this DIV -->

In [4]:
open FSharp.Stats

let smootheTemp ws order (days,tm,tmUpper,tmLower) =
    let tm' = Signal.Filtering.savitzkyGolay ws order 0 1 tm
    let tmUpper' = Signal.Filtering.savitzkyGolay ws order 0 1 tmUpper
    let tmLower' = Signal.Filtering.savitzkyGolay ws order 0 1 tmLower
    days,tm',tmUpper',tmLower'

let smoothedChart =
    processedData
    |> smootheTemp 31 4
    |> createTempChart 

smoothedChart |> GenericChart.toChartHTML


<!-- Plotly chart will be drawn inside this DIV -->